In [1]:
# Лабораторная работа 1
import pandas as pd
import numpy as np

In [2]:
data = pd.read_excel(r"C:\Users\Cyber\Downloads\daily-weather-dataset_chronological-order.xlsx", sheet_name="daily")

FileNotFoundError: [Errno 2] No such file or directory: 'C:\\Users\\Cyber\\Downloads\\daily-weather-dataset_chronological-order.xlsx'

In [ ]:
data.tail()

In [ ]:
data.head()

In [ ]:
data.shape # Параметр .shape показывает размерность датафрейма

In [ ]:
data.size  # Параметр .size показывает количество элементов в датафрейме

In [ ]:
data.count() # Метод count считает сколько всего непустых записей в каждом столбце

In [ ]:
data.info() # Метод .info() показывает тип каждого столбца и занимаемую память

In [ ]:
data.dtypes # Параметр .dtypes показывает просто тип каждого столбца

In [ ]:
data.isna().head() # Метод .isna() вместо каждого значения подставит True (значение NaN) или False (действительное значение)

In [ ]:
data.isna().sum() # Подсчитаем количество пропусков в каждом столбце с помощью метода .sum()

In [ ]:
proc = data.isna().sum().sum() # Подсчитаем сколько всего пропусков (во всех столбцах) в нашем датафрейме
print(proc) # Отобразим количество посчитанных пропусков

In [ ]:
proc = data.isna().sum().sum() / data.size
print(round(100*proc,1), '%', sep='')

In [ ]:
df = pd.DataFrame(data)
# Функция для удаления выбросов по IQR
def remove_outliers(df, column):
    Q1 = df[column].quantile(0.25)
    Q3 = df[column].quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    return df[(df[column] >= lower_bound) & (df[column] <= upper_bound)]

# Удаляем выбросы из указанных столбцов
columns_to_clean = ["Cloud coverage"]
for col in columns_to_clean:
    df = remove_outliers(df, col)

In [ ]:
df = df.dropna(axis=1, how='all')

In [ ]:
df

In [ ]:
#3 Для прогнозирования солнечной генерации применена группировка по месяцу и времени года – чтобы учитывать сезонность выработки.
df["Date"] = pd.to_datetime(df["Date"]) # Преобразуем столбец 'Date' в формат datetime
df["Month"] = df["Date"].dt.month # Добавляем столбец 'Month' для группировки по месяцам
df_monthly = df.groupby("Month").mean() # Группируем по месяцу и вычисляем средние значения
df_monthly

In [ ]:
#5
import matplotlib.pyplot as plt
import seaborn as sns


In [ ]:
# 5.1 
# Выбираем числовые столбцы, исключая "Month"
numeric_features = df.select_dtypes(include=["number"]).columns
numeric_features = numeric_features.drop("Month")  # Убираем "Month"

# Строим графики для всех числовых признаков (кроме "Month")
for col in numeric_features:
    plt.figure(figsize=(14, 4))

    # График плотности (KDE)
    plt.subplot(121)
    sns.kdeplot(data=df, x=col)
    plt.title(f"Распределение: {col}")

    # Boxplot (ящик с усами)
    plt.subplot(122)
    sns.boxplot(data=df, x=col)
    plt.title(f"Boxplot: {col}")

    plt.show()

#plt.figure(figsize=(8, 5))
#sns.histplot(df['Visibility'], bins=20, kde=True)
#plt.title("Гистограмма распределения параметра видимости")
#plt.show()

In [ ]:
# 5.3. Матрица корреляции
# Позволяет увидеть, как связаны между собой числовые переменные и для поиска зависимостей между погодными параметрами
# Чем ближе значение к 1 или -1, тем сильнее положительная или отрицательная корреляция
plt.figure(figsize=(8, 5))
sns.heatmap(df_monthly.corr(), annot=True, cmap='coolwarm', fmt=".2f")
plt.title("Матрица корреляции погодных параметров")
plt.show()

In [ ]:
# 5.4. Диаграмма рассеяния облачности и солнечной энергии
# Показывает взаимосвязь между облачностью и уровнем солнечной энергии.
plt.figure(figsize=(8, 5))
sns.scatterplot(x=df['Cloud coverage'], y=df['Solar energy'])
plt.title("Диаграмма рассеяния: Облачность vs Солнечная энергия")
plt.show()


In [ ]:
# 5.5. Среднее значение облачности по месяцам
#Позволяет проанализировать сезонные тренды облачности.
#Позволяет быстро увидеть, в какие месяцы облачность выше или ниже.
plt.figure(figsize=(8, 5))
sns.barplot(x=df['Month'], y=df['Cloud coverage'], estimator=sum)
plt.title("Среднее значение облачности по месяцам")
plt.show()


In [ ]:
from sklearn.feature_selection import VarianceThreshold

# Оставляем только числовые признаки
numeric_features = df.select_dtypes(include=["number"])

# Удаляем признаки с дисперсией ниже 0.01
selector = VarianceThreshold(threshold=0.01)
df_var = selector.fit_transform(numeric_features)

# Получаем оставшиеся названия признаков
selected_features = numeric_features.columns[selector.get_support()]
df_selected = df[selected_features]


In [ ]:
from sklearn.feature_selection import SelectKBest, f_regression

# Убираем столбец с датами и выбираем только числовые признаки
X = df.select_dtypes(include=["number"]).drop(columns=["Solar energy"])  
y = df["Solar energy"]  # Целевая переменная

# Отбор 5 лучших признаков
selector = SelectKBest(score_func=f_regression, k=5)
X_new = selector.fit_transform(X, y)

# Выводим выбранные признаки
selected_features = X.columns[selector.get_support()]
print("Выбранные признаки:", selected_features)


In [ ]:
from sklearn.feature_selection import RFE
from sklearn.linear_model import LinearRegression

model = LinearRegression()
rfe = RFE(model, n_features_to_select=5)
X_rfe = rfe.fit_transform(X, y)

selected_features = X.columns[rfe.support_]
print("Новые лучшие признаки:", selected_features)



In [ ]:
df["Temp_Cloud"] = df["Temperature"] * df["Cloud coverage"]
print("\nDataFrame с добавленным признаком 'Temp_Cloud':")
df

In [ ]:
# 7
plt.figure(figsize=(8, 5))
sns.histplot(df["Solar energy"], bins=30, kde=True)
plt.title("Распределение целевой переменной (Solar Energy)")
plt.xlabel("Solar Energy")
plt.ylabel("Частота")
plt.show()

In [ ]:
plt.figure(figsize=(12, 6))
sns.boxplot(x=df["Month"], y=df["Solar energy"])
plt.title("Распределение Solar Energy по месяцам")
plt.show()


In [ ]:
#8
from sklearn.model_selection import train_test_split
df = df.drop(columns=["Date"])
df = df.drop(columns=["Month"])
y = df["Solar energy"]
# Удалим целевую переменную
X = df.drop(columns=["Solar energy"])


# Разбиение (80% train, 20% test)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
# Вывод размеров получившихся выборок
print(f"Размер X_train: {X_train.shape}")
print(f"Размер X_test: {X_test.shape}")
print(f"Размер y_train: {y_train.shape}")
print(f"Размер y_test: {y_test.shape}")
print("Обучающая выборка X:")
print(X_train)
print("\nТестовая выборка X:")
print(X_test)
print("\nОбучающая выборка y:")
print(y_train)
print("\nТестовая выборка y:")
print(y_test)


In [ ]:
# Лабораторная работа 2
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

# Модели машинного обучения
from sklearn.neighbors import KNeighborsRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostRegressor
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV, KFold
from sklearn.neural_network import MLPRegressor
cv = KFold(n_splits=5, shuffle=True, random_state=42)


In [ ]:
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)


In [ ]:
# Knn
knn_params = {
    'n_neighbors': [3, 5, 7, 9],
    'weights': ['uniform', 'distance'],
    'metric': ['euclidean', 'manhattan']
}
knn_grid = GridSearchCV(KNeighborsRegressor(), knn_params, cv=cv, scoring='r2', n_jobs=-1)
knn_grid.fit(X_train, y_train)
print("Best KNN:", knn_grid.best_params_, "Best R²:", knn_grid.best_score_)

In [ ]:
# Дерево решений
dt_params = {
    'max_depth': [3, 5, 10, 15],
    'min_samples_split': [2, 5, 10],
    'min_samples_leaf': [1, 2, 5]
}
dt_grid = GridSearchCV(DecisionTreeRegressor(random_state=42), dt_params, cv=cv, scoring='r2', n_jobs=-1)
dt_grid.fit(X_train, y_train)
print("Best Decision Tree:", dt_grid.best_params_, "Best R²:", dt_grid.best_score_)


In [ ]:
# Случайный лес
rf_params = {
    'n_estimators': [100, 200, 300],
    'max_depth': [5, 10, 15],
    'min_samples_split': [2, 5, 10]
}
rf_grid = GridSearchCV(RandomForestRegressor(random_state=42), rf_params, cv=cv, scoring='r2', n_jobs=-1)
rf_grid.fit(X_train, y_train)
print("Best Random Forest:", rf_grid.best_params_, "Best R²:", rf_grid.best_score_)

In [ ]:
# Градиентный бустинг
cat_params = {
    'iterations': [100, 500, 1000],
    'learning_rate': [0.01, 0.05, 0.1],
    'depth': [4, 6, 8]
}
cat_grid = RandomizedSearchCV(CatBoostRegressor(verbose=0, random_state=42), cat_params, cv=cv, scoring='r2', n_jobs=-1, n_iter=10)
cat_grid.fit(X_train, y_train)
print("Best CatBoost:", cat_grid.best_params_, "Best R²:", cat_grid.best_score_)

In [ ]:
# Нейронная сеть
mlp_params = {
    'hidden_layer_sizes': [(50,), (100,), (50, 50)],
    'activation': ['relu', 'tanh'],
    'alpha': [0.0001, 0.001, 0.01]
}
mlp_grid = RandomizedSearchCV(MLPRegressor(max_iter=5500, random_state=42), mlp_params, cv=cv, scoring='r2', n_jobs=-1, n_iter=10)
mlp_grid.fit(X_train, y_train)
print("Best MLP:", mlp_grid.best_params_, "Best R²:", mlp_grid.best_score_)


In [ ]:
# Сравнение моделей
models = ["KNN", "Decision Tree", "Random Forest", "CatBoost", "Neural Network"]
scores = [
    knn_grid.best_score_,
    dt_grid.best_score_,
    rf_grid.best_score_,
    cat_grid.best_score_,
    mlp_grid.best_score_
]

plt.figure(figsize=(10, 5))
sns.barplot(x=models, y=scores)
plt.ylabel("R2 Score")
plt.title("Сравнение моделей машинного обучения")
plt.show()


In [ ]:
# Лабораторная работа №3 - Оценка моделей
knn_best = knn_grid.best_estimator_
dt_best = dt_grid.best_estimator_
rf_best = rf_grid.best_estimator_
cat_best = cat_grid.best_estimator_
mlp_best = mlp_grid.best_estimator_
def evaluate_model(model, X_test, y_test):
    y_pred = model.predict(X_test)
    mae = mean_absolute_error(y_test, y_pred)
    mse = mean_squared_error(y_test, y_pred)
    rmse = np.sqrt(mse)
    mape = np.mean(np.abs((y_test - y_pred) / y_test)) * 100
    r2 = r2_score(y_test, y_pred)
    return {'MAE': mae, 'MSE': mse, 'RMSE': rmse, 'MAPE': mape, 'R2': r2}

models = {'KNN': knn_best, 'Decision Tree': dt_best, 'Random Forest': rf_best, 'CatBoost': cat_best, 'MLP': mlp_best}

for name, model in models.items():
    results = evaluate_model(model, X_test, y_test)
    print(f"{name} Evaluation: {results}")



In [ ]:
# Визуализация результатов
# Словарь для хранения результатов
metrics = {'Model': [], 'MAE': [], 'MSE': [], 'RMSE': [], 'MAPE': [], 'R2': []}

# Оценка каждой модели
for name, model in models.items():
    results = evaluate_model(model, X_test, y_test)
    metrics['Model'].append(name)
    for key in results:
        metrics[key].append(results[key])

# Преобразование в DataFrame
metrics_df = pd.DataFrame(metrics)
metrics_df.set_index('Model', inplace=True)

# Названия метрик и их описания для графиков
metric_labels = {
    'MAE': 'Средняя абсолютная ошибка (MAE)',
    'MSE': 'Среднеквадратическая ошибка (MSE)',
    'RMSE': 'Корень из MSE (RMSE)',
    'MAPE': 'Средняя абсолютная процентная ошибка (MAPE)',
    'R2': 'Коэффициент детерминации (R²)'
}

# Отображение каждого графика отдельно
for metric in metrics_df.columns:
    plt.figure(figsize=(8, 5))
    sns.barplot(
        x=metrics_df.index, 
        y=metrics_df[metric], 
        hue=metrics_df.index,  # Добавляем hue
        palette='viridis', 
        edgecolor='black',
        legend=False  # Отключаем легенду, так как цвета соответствуют x
    )
    plt.title(f'Сравнение моделей по {metric_labels[metric]}', fontsize=14)
    plt.xlabel("Модель", fontsize=12)
    plt.ylabel(metric_labels[metric], fontsize=12)
    plt.xticks(rotation=45)
    plt.grid(axis='y', linestyle='--', alpha=0.7)
    plt.show()


# Визуализация фактических vs предсказанных значений для лучшей модели (по R²)
best_model_name = metrics_df.sort_values(by='R2', ascending=False).index[0]
best_model = models[best_model_name]

y_pred_best = best_model.predict(X_test)

plt.figure(figsize=(8, 8))
sns.scatterplot(x=y_test, y=y_pred_best, alpha=0.6)
plt.plot([min(y_test), max(y_test)], [min(y_test), max(y_test)], '--r', label="Идеальное предсказание")
plt.xlabel("Фактические значения", fontsize=12)
plt.ylabel("Предсказанные значения", fontsize=12)
plt.title(f"Фактические vs. Предсказанные ({best_model_name})", fontsize=14)
plt.legend()
plt.grid(True)
plt.show()

In [ ]:
# Лабораторная работа №4
df = df.drop(columns=["Altimeter"])
df = df.drop(columns=["Temp_Cloud"])
y = df["Solar energy"]
X = df.drop(columns=["Solar energy"])
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)


In [ ]:
# Knn

knn_params = {

    'n_neighbors': [3, 5, 7, 9],

    'weights': ['uniform', 'distance'],

    'metric': ['euclidean', 'manhattan']

}

knn_grid = GridSearchCV(KNeighborsRegressor(), knn_params, cv=cv, scoring='r2', n_jobs=-1)

knn_grid.fit(X_train, y_train)

print("Best KNN:", knn_grid.best_params_, "Best R²:", knn_grid.best_score_)

# Дерево решений

dt_params = {

    'max_depth': [3, 5, 10, 15],

    'min_samples_split': [2, 5, 10],

    'min_samples_leaf': [1, 2, 5]

}

dt_grid = GridSearchCV(DecisionTreeRegressor(random_state=42), dt_params, cv=cv, scoring='r2', n_jobs=-1)

dt_grid.fit(X_train, y_train)

print("Best Decision Tree:", dt_grid.best_params_, "Best R²:", dt_grid.best_score_)

# Случайный лес

rf_params = {

    'n_estimators': [100, 200, 300],

    'max_depth': [5, 10, 15],

    'min_samples_split': [2, 5, 10]

}

rf_grid = GridSearchCV(RandomForestRegressor(random_state=42), rf_params, cv=cv, scoring='r2', n_jobs=-1)

rf_grid.fit(X_train, y_train)

print("Best Random Forest:", rf_grid.best_params_, "Best R²:", rf_grid.best_score_)

# Градиентный бустинг

cat_params = {

    'iterations': [100, 500, 1000],

    'learning_rate': [0.01, 0.05, 0.1],

    'depth': [4, 6, 8]

}

cat_grid = RandomizedSearchCV(CatBoostRegressor(verbose=0, random_state=42), cat_params, cv=cv, scoring='r2', n_jobs=-1, n_iter=10)

cat_grid.fit(X_train, y_train)

print("Best CatBoost:", cat_grid.best_params_, "Best R²:", cat_grid.best_score_)

# Нейронная сеть

mlp_params = {

    'hidden_layer_sizes': [(50,), (100,), (50, 50)],

    'activation': ['relu', 'tanh'],

    'alpha': [0.0001, 0.001, 0.01]

}

mlp_grid = RandomizedSearchCV(MLPRegressor(max_iter=5500, random_state=42), mlp_params, cv=cv, scoring='r2', n_jobs=-1, n_iter=10)

mlp_grid.fit(X_train, y_train)

print("Best MLP:", mlp_grid.best_params_, "Best R²:", mlp_grid.best_score_)


In [ ]:
knn_best = knn_grid.best_estimator_
dt_best = dt_grid.best_estimator_
rf_best = rf_grid.best_estimator_
cat_best = cat_grid.best_estimator_
mlp_best = mlp_grid.best_estimator_
def evaluate_model(model, X_test, y_test):
    y_pred = model.predict(X_test)
    mae = mean_absolute_error(y_test, y_pred)
    mse = mean_squared_error(y_test, y_pred)
    rmse = np.sqrt(mse)
    mape = np.mean(np.abs((y_test - y_pred) / y_test)) * 100
    r2 = r2_score(y_test, y_pred)
    return {'MAE': mae, 'MSE': mse, 'RMSE': rmse, 'MAPE': mape, 'R2': r2}

models = {'KNN': knn_best, 'Decision Tree': dt_best, 'Random Forest': rf_best, 'CatBoost': cat_best, 'MLP': mlp_best}

for name, model in models.items():
    results = evaluate_model(model, X_test, y_test)
    print(f"{name} Evaluation: {results}")




In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

# Список моделей и их названий
models = {
    "KNN": knn_best,
    "Decision Tree": dt_best,
    "Random Forest": rf_best,
    "CatBoost": cat_best,
    "MLP": mlp_best
}

# Создаем DataFrame для предсказанных значений
predictions_df = pd.DataFrame({"Actual": y_test})

# Генерируем предсказания для каждой модели
for name, model in models.items():
    predictions_df[name] = model.predict(X_test)

# Выводим первые 10 строк предсказаний
print(predictions_df.head(10))

# Визуализация предсказаний
plt.figure(figsize=(12, 6))
plt.plot(predictions_df["Actual"].values, label="Actual", color="black", linewidth=2)

for name in models.keys():
    plt.plot(predictions_df[name].values, label=name, linestyle="--")

plt.legend()
plt.title("Actual vs Predicted Values")
plt.xlabel("Samples")
plt.ylabel("Solar Energy Output")
plt.show()


In [ ]:
import pickle

# Список моделей и их названий
models = {
    "KNN": knn_best,
    "Decision_Tree": dt_best,
    "Random_Forest": rf_best,
    "CatBoost": cat_best,
    "MLP": mlp_best
}

# Сохраняем каждую модель в файл .pkl
for name, model in models.items():
    with open(f"{name}.pkl", "wb") as file:
        pickle.dump(model, file)

print("Все модели сохранены в формате .pkl!")


In [ ]:
df